In [1]:
import csv
from zipfile import ZipFile
from io import TextIOWrapper
import pandas as pd
import random
import os, math


In [2]:
class ZippedCSVReader:
    def __init__(self,name):
        self.paths=[]
        self.filename=name
        with ZipFile(name) as zf:
            for info in zf.infolist():
                self.paths.append(info.filename)
    
    def lines(self, name):
        with ZipFile(self.filename) as zf:
            with zf.open(name) as f:
                for line in TextIOWrapper(f):
                    yield line
        
    def csv_iter(self,CSVname=None):
        if CSVname!=None:
            with ZipFile(self.filename) as zf:
                with zf.open(CSVname) as f:
                    tio=TextIOWrapper(f)
                    reader=csv.DictReader(tio)
                    for row in reader:
                        yield row
        else:
            for CSVname in self.paths:
                with ZipFile(self.filename) as zf:
                    with zf.open(CSVname,"r") as f:
                        tio=TextIOWrapper(f)
                        reader=csv.DictReader(tio)
                        for row in reader:
                            yield row


In [3]:
data_reader = ZippedCSVReader("mini.zip")
tree_reader = ZippedCSVReader("trees.zip")

In [4]:
print(data_reader.paths) # in alphabetical order!

['wi.csv', 'il.csv', 'la.csv']


In [5]:
print(tree_reader.paths)

['simple.txt', 'good.txt', 'bad.txt', 'tree1.txt', 'tree2.txt', 'tree3.txt', 'tree4.txt', 'tree5.txt', 'tree6.txt', 'tree7.txt']


In [6]:
for row in tree_reader.lines("simple.txt"):
    print(row)

|--- amount <= 200

|   |--- income <= 35

|   |   |--- class: 0

|   |--- income >  35

|   |   |--- class: 1

|--- amount >  200

|   |--- income <= 70

|   |   |--- class: 0

|   |--- income >  70

|   |   |--- class: 1


In [7]:
for i in data_reader.csv_iter():
    print(i)

OrderedDict([('as_of_year', '2017'), ('respondent_id', '146672'), ('agency_name', 'Consumer Financial Protection Bureau'), ('agency_abbr', 'CFPB'), ('agency_code', '9'), ('loan_type_name', 'Conventional'), ('loan_type', '1'), ('property_type_name', 'One-to-four family dwelling (other than manufactured housing)'), ('property_type', '1'), ('loan_purpose_name', 'Home purchase'), ('loan_purpose', '1'), ('owner_occupancy_name', 'Owner-occupied as a principal dwelling'), ('owner_occupancy', '1'), ('loan_amount_000s', '100'), ('preapproval_name', 'Not applicable'), ('preapproval', '3'), ('action_taken_name', 'Application denied by financial institution'), ('action_taken', '3'), ('state_name', 'Wisconsin'), ('state_abbr', 'WI'), ('state_code', '55'), ('county_name', 'Chippewa County'), ('county_code', '17'), ('applicant_ethnicity_name', 'Information not provided by applicant in mail, Internet, or telephone application'), ('applicant_ethnicity', '3'), ('co_applicant_ethnicity_name', 'No co-appl

In [8]:
class Loan:
    def __init__(self, amount, purpose, race, income, decision):
        self.amount=amount
        self.purpose=purpose
        self.race=race
        self.income=income
        self.decision=decision

    def __repr__(self):
        return("Loan({}, '{}', '{}', '{}', '{}')".format(self.amount,self.purpose,self.race,self.income,self.decision))

    def __getitem__(self, lookup):
        if lookup=="amount":
            return self.amount
        if lookup=="purpose":
            return self.purpose
        if lookup=="race":
            return self.race
        if lookup=="income":
            return self.income
        if lookup=="decision":
            return self.decision

In [9]:
def get_bank_names():
    bank_names=[]
    loans=ZippedCSVReader("loans.zip")
    for row in loans.csv_iter():
        bank_names.append(row["agency_abbr"])
    bank_names=list(set(bank_names))
    bank_names.sort()
    return(bank_names)

bank_names = get_bank_names()

class Bank:
    def __init__(self,agency_abbr,reader):
        self.reader=reader
        self.agency_abbr=agency_abbr
        
    def loan_iter(self):
        for row in self.reader.csv_iter():
            if row["agency_abbr"]==self.agency_abbr:
                row['respondent_id']=Loan(row["loan_amount_000s"],row["loan_purpose"], row["applicant_race_name_1"], row["applicant_income_000s"],row["action_taken_name"])
                yield row['respondent_id']
    
    def loan_filter(self, loan_min, loan_max, loan_purpose):
        for row in self.reader.csv_iter():
            if row["loan_amount_000s"]>=loan_min&row["loan_amount_000s"]<=loan_max&row["loan_purpose"]==loan_purpose:
                yield row['respondednt_id']

In [10]:
reader = ZippedCSVReader('loans.zip')
b = Bank("HUD", reader)
for loan in b.loan_iter():
    print(loan)


Loan(89, '3', 'White', '96', 'Application denied by financial institution')
Loan(82, '1', 'White', '74', 'Loan originated')
Loan(80, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '60', 'File closed for incompleteness')
Loan(146, '3', 'White', '82', 'Loan originated')
Loan(68, '3', 'White', '13', 'Application denied by financial institution')
Loan(164, '3', 'White', '70', 'Application denied by financial institution')
Loan(120, '3', 'White', '58', 'Application denied by financial institution')
Loan(55, '1', 'Information not provided by applicant in mail, Internet, or telephone application', '39', 'Application withdrawn by applicant')
Loan(70, '3', 'White', '21', 'Loan originated')
Loan(220, '1', 'Information not provided by applicant in mail, Internet, or telephone application', '101', 'Application withdrawn by applicant')
Loan(137, '3', 'White', '', 'Application denied by financial institution')
Loan(70, '3', 'Information not provided by appl

Loan(125, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '58', 'Loan originated')
Loan(136, '1', 'White', '61', 'Loan originated')
Loan(247, '3', 'Native Hawaiian or Other Pacific Islander', '31', 'Application denied by financial institution')
Loan(279, '3', 'White', '108', 'Loan originated')
Loan(141, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '48', 'Application denied by financial institution')
Loan(271, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '', 'Loan originated')
Loan(113, '3', 'White', '52', 'Loan originated')
Loan(117, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '75', 'Application withdrawn by applicant')
Loan(82, '3', 'White', '32', 'Application denied by financial institution')
Loan(143, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '77', 'Loan origin

Loan(172, '3', 'White', '70', 'Application denied by financial institution')
Loan(134, '1', 'White', '34', 'Application withdrawn by applicant')
Loan(220, '1', 'White', '45', 'Loan originated')
Loan(216, '3', 'White', '70', 'Loan originated')
Loan(82, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '', 'Application denied by financial institution')
Loan(224, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '74', 'Application denied by financial institution')
Loan(217, '1', 'White', '91', 'Loan originated')
Loan(253, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '75', 'Loan originated')
Loan(86, '1', 'Asian', '23', 'Application denied by financial institution')
Loan(242, '3', 'White', '108', 'Loan originated')
Loan(251, '1', 'White', '68', 'Loan originated')
Loan(285, '3', 'White', '126', 'Application denied by financial institution')
Loan(214, '1', 'White', '58

Loan(128, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '42', 'Loan originated')
Loan(107, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '70', 'Application denied by financial institution')
Loan(164, '3', 'White', '43', 'Application denied by financial institution')
Loan(424, '1', 'White', '245', 'Loan originated')
Loan(140, '1', 'Not applicable', '', 'Loan purchased by the institution')
Loan(102, '2', 'White', '30', 'Application withdrawn by applicant')
Loan(168, '1', 'White', '42', 'Loan originated')
Loan(185, '1', 'Not applicable', '', 'Loan purchased by the institution')
Loan(160, '1', 'White', '53', 'Loan originated')
Loan(333, '3', 'White', '168', 'Loan originated')
Loan(481, '3', 'White', '116', 'Loan originated')
Loan(257, '1', 'White', '117', 'Loan originated')
Loan(424, '1', 'Black or African American', '102', 'Loan originated')
Loan(246, '3', 'Black or African American', '110', 'Applicati

Loan(369, '3', 'White', '123', 'Loan originated')
Loan(424, '1', 'White', '134', 'Loan originated')
Loan(228, '1', 'White', '81', 'Loan originated')
Loan(128, '3', 'White', '', 'Loan originated')
Loan(212, '3', 'White', '', 'File closed for incompleteness')
Loan(268, '3', 'White', '180', 'Loan originated')
Loan(366, '1', 'White', '81', 'Loan originated')
Loan(87, '1', 'White', '33', 'Application denied by financial institution')
Loan(244, '3', 'White', '133', 'Loan originated')
Loan(228, '3', 'White', '126', 'Loan originated')
Loan(85, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '70', 'Loan originated')
Loan(233, '3', 'White', '57', 'Loan originated')
Loan(377, '3', 'White', '122', 'Loan originated')
Loan(136, '1', 'White', '68', 'Loan originated')
Loan(211, '3', 'White', '61', 'Application withdrawn by applicant')
Loan(262, '3', 'White', '73', 'Loan originated')
Loan(164, '3', 'White', '116', 'Loan originated')
Loan(174, '1', 'White', '72'

...

Loan(212, '1', 'White', '64', 'Loan originated')
Loan(182, '1', 'Black or African American', '77', 'Loan originated')
Loan(113, '3', 'White', '65', 'Loan originated')
Loan(142, '1', 'Black or African American', '37', 'Loan originated')
Loan(158, '3', 'White', '71', 'Loan originated')
Loan(137, '1', 'Black or African American', '37', 'Application withdrawn by applicant')
Loan(108, '1', 'Black or African American', '47', 'Loan originated')
Loan(103, '1', 'White', '71', 'File closed for incompleteness')
Loan(121, '1', 'White', '59', 'Loan originated')
Loan(135, '1', 'Black or African American', '38', 'Loan originated')
Loan(303, '1', 'White', '105', 'Loan originated')
Loan(343, '1', 'White', '194', 'Loan purchased by the institution')
Loan(356, '1', 'White', '187', 'Loan originated')
Loan(85, '1', 'Black or African American', '27', 'Loan originated')
Loan(94, '1', 'White', '24', 'Loan originated')
Loan(195, '1', 'White', '47', 'Loan originated')
Loan(104, '3', 'White', '44', 'Application 

Loan(105, '1', 'White', '139', 'Loan originated')
Loan(182, '1', 'Not applicable', '', 'Loan purchased by the institution')
Loan(257, '1', 'White', '105', 'Loan originated')
Loan(50, '3', 'White', '48', 'Loan originated')
Loan(141, '3', 'White', '41', 'Loan originated')
Loan(148, '1', 'White', '187', 'Loan originated')
Loan(96, '3', 'White', '66', 'Loan originated')
Loan(132, '1', 'White', '120', 'Application denied by financial institution')
Loan(106, '1', 'White', '47', 'Loan originated')
Loan(196, '1', 'White', '33', 'Loan originated')
Loan(127, '1', 'White', '102', 'Application denied by financial institution')
Loan(136, '1', 'White', '42', 'Loan originated')
Loan(175, '1', 'White', '40', 'Loan originated')
Loan(49, '1', 'White', '135', 'File closed for incompleteness')
Loan(215, '1', 'White', '65', 'Loan originated')
Loan(65, '3', 'White', '75', 'Loan originated')
Loan(188, '3', 'White', '51', 'Application denied by financial institution')
Loan(225, '1', 'Information not provided 

Loan(125, '3', 'White', '51', 'Loan originated')
Loan(128, '3', 'White', '120', 'Loan originated')
Loan(80, '1', 'Black or African American', '173', 'Application denied by financial institution')
Loan(220, '1', 'White', '127', 'Loan originated')
Loan(150, '2', 'Information not provided by applicant in mail, Internet, or telephone application', '48', 'Application withdrawn by applicant')
Loan(232, '1', 'White', '75', 'Loan originated')
Loan(155, '3', 'White', '144', 'Loan originated')
Loan(234, '1', 'White', '101', 'Application denied by financial institution')
Loan(164, '1', 'Black or African American', '38', 'Loan originated')
Loan(214, '3', 'Not applicable', '', 'Loan purchased by the institution')
Loan(179, '3', 'White', '61', 'Loan originated')
Loan(78, '1', 'Information not provided by applicant in mail, Internet, or telephone application', '31', 'Application denied by financial institution')
Loan(151, '3', 'Black or African American', '', 'Loan originated')
Loan(176, '1', 'White'

Loan(96, '3', 'White', '60', 'Loan originated')
Loan(53, '1', 'Black or African American', '14', 'Application denied by financial institution')
Loan(243, '1', 'White', '120', 'Loan originated')
Loan(104, '3', 'White', '58', 'Loan originated')
Loan(162, '3', 'White', '', 'Application withdrawn by applicant')
Loan(35, '1', 'Asian', '21', 'Application denied by financial institution')
Loan(42, '1', 'Black or African American', '47', 'Application denied by financial institution')
Loan(249, '3', 'White', '96', 'Loan originated')
Loan(183, '1', 'White', '65', 'Loan originated')
Loan(158, '1', 'White', '38', 'Loan originated')
Loan(306, '3', 'Not applicable', '', 'Loan purchased by the institution')
Loan(131, '1', 'Not applicable', '47', 'Loan purchased by the institution')
Loan(159, '3', 'White', '55', 'Application withdrawn by applicant')
Loan(180, '1', 'White', '89', 'Loan originated')
Loan(83, '3', 'White', '113', 'Loan originated')
Loan(156, '3', 'White', '83', 'Loan originated')
Loan(28

Loan(630, '3', 'White', '89', 'Application withdrawn by applicant')
Loan(142, '1', 'Black or African American', '41', 'Loan originated')
Loan(134, '1', 'Not applicable', '', 'Loan purchased by the institution')
Loan(144, '1', 'Black or African American', '47', 'Application withdrawn by applicant')
Loan(76, '1', 'White', '86', 'Loan originated')
Loan(204, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '37', 'Loan originated')
Loan(43, '1', 'Black or African American', '36', 'Application denied by financial institution')
Loan(97, '3', 'Black or African American', '18', 'Loan originated')
Loan(165, '3', 'White', '90', 'Loan originated')
Loan(49, '1', 'Black or African American', '25', 'File closed for incompleteness')
Loan(105, '1', 'White', '37', 'Loan originated')
Loan(71, '1', 'White', '38', 'Loan originated')
Loan(75, '3', 'Information not provided by applicant in mail, Internet, or telephone application', '32', 'Application denied by financi

In [11]:
class SimplePredictor():
    def __init__(self):
        self.num_approved=0
    
    def predict(self, loan):
        if loan["loan_purpose"]=="Home improvement":
            self.num_approved+=1
            return True
        else:
            return False

    def getApproved(self):
        return self.num_approved

In [42]:
#class Node copied from https://tyler.caraza-harter.com/cs320/f20/reading/lec-12-search-trees.html
class Node:
    def __init__(self, val):
        self.val = val
        self.left = None
        self.right = None
    
    def to_graphviz(self, g=None):
        if g == None:
            g = Digraph()
            
        # draw self
        g.node(repr(self.val))
    
        for label, child in [("L", self.left), ("R", self.right)]:
            if child != None:
                # draw child, recursively
                child.to_graphviz(g)
                
                # draw edge from self to child
                g.edge(repr(self.val), repr(child.val), label=label)
        return g
    
    def _repr_svg_(self):
        return self.to_graphviz()._repr_svg_()

class DTree(SimplePredictor):
    def __init__(self):
        SimplePredictor.__init__(self)
        self.root=None
    def readTree(self,reader, path):
        node_depths={}
        
        for line in reader.lines(path):
            line=(line.split("---"))
            depth=(len(line[0].split("   ")))
            node_depths[depth]=line[1]
            print(node_depths)
            if len(node_depths)==1:
                root=Node(line[1])
            else:
                if 
            
    def predict(self,data):
        pass
    def getDisapproved(self):
        pass

In [43]:
tree_reader = ZippedCSVReader('trees.zip')
dtree = DTree()
dtree.readTree(tree_reader, "simple.txt")
dtree.predict(loan)

{1: ' amount <= 200\n'}
{1: ' amount <= 200\n', 2: ' income <= 35\n'}
{1: ' amount <= 200\n', 2: ' income <= 35\n', 3: ' class: 0\n'}
{1: ' amount <= 200\n', 2: ' income >  35\n', 3: ' class: 0\n'}
{1: ' amount <= 200\n', 2: ' income >  35\n', 3: ' class: 1\n'}
{1: ' amount >  200\n', 2: ' income >  35\n', 3: ' class: 1\n'}
{1: ' amount >  200\n', 2: ' income <= 70\n', 3: ' class: 1\n'}
{1: ' amount >  200\n', 2: ' income <= 70\n', 3: ' class: 0\n'}
{1: ' amount >  200\n', 2: ' income >  70\n', 3: ' class: 0\n'}
{1: ' amount >  200\n', 2: ' income >  70\n', 3: ' class: 1'}


In [25]:
for row in tree_reader.lines("simple.txt"):
    print(row)

|--- amount <= 200

|   |--- income <= 35

|   |   |--- class: 0

|   |--- income >  35

|   |   |--- class: 1

|--- amount >  200

|   |--- income <= 70

|   |   |--- class: 0

|   |--- income >  70

|   |   |--- class: 1
